# Imports

In [1]:
import pandas as pd
import os
import io
from utils import read_file
from utils import convert_to_unsigned_np
from PIL import Image
import numpy as np
from scipy import signal 
import matplotlib as mpl 
import matplotlib.pyplot as plt 
import requests  # pip install requests 
import sys
import numpy
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier as RF
import scipy
import torch
from utils import Conv
from utils import make_conv_feat
import subprocess

#/data/isip/www/isip/courses/temple/ece_8527/exams/current/exam_04/results/auchincloss_mary

# variable names

In [3]:
DIR = "/data/isip/www/isip/courses/temple/ece_8527/resources/data/set_15/lists"
N = 99487


# Data Loading

### Features

In [4]:
eval_list = read_file(os.path.join(DIR,"data_eval.list"))


eval_list=eval_list.strip().split("\n") #file names - strip gets rid of blank space - split turns it into a list of strings



In [5]:
eval_array = [np.frombuffer(read_file(x),dtype=np.short).reshape((-1,8)) for j,x in enumerate(eval_list)] #reading in .dat to list of arrays


In [6]:
len(eval_array)

20000

## Data processing

In [7]:
#train_healthy_array 
#train_unhealthy_array 

#seperate the channels and turn list of arrays into single array
#first dimension is the data 
#second dimension is the time
#3rd dimension is channels 

X  = np.stack(eval_array, axis = 2).transpose((2,0,1))


X.shape


(20000, 2200, 8)

# make model   

network doing one layer 


In [8]:
from torch import nn 
class Model(nn.Module):

    # function: init
    #
    # arguments: input_size - int representing size of input
    #            hidden_size - number of nodes in the hidden layer
    #            num_classes - number of classes to classify
    #
    # return: none
    #
    # This method is the main function.
    #
    def __init__(self):

        # inherit the superclass properties/methods
        #
        super(Model, self).__init__()

        self.conv1 = nn.Conv1d(8, 32, 3,stride = 3) # 8 input channels, 64 output channels, 3x3 kernel, stride 1
        self.maxpool1 = nn.MaxPool1d(3)
        self.relu1 = nn.ReLU()
        self.conv2 = nn.Conv1d(32, 16, 3,stride = 3)
        self.maxpool2 = nn.MaxPool1d(3)
        self.relu2 = nn.ReLU()
    
        self.fc1 = nn.Linear(432, 64)
        self.relu3 = nn.ReLU()
        self.fc2 = nn.Linear(64, 6)

    def forward(self, data):
        data = data.permute(0, 2, 1)

        x = self.conv1(data)
        x = self.maxpool1(x)
        x = self.relu1(x)
        x = self.conv2(x)
        x = self.maxpool2(x)
        x = self.relu2(x)   


        x = x.view(x.size(0), -1)
    
        x = self.fc1(x)
        x = self.relu3(x)
        x = self.fc2(x)

        x = torch.sigmoid(x)
        return x
    

from torch import nn 
class Model(nn.Module):

    # function: init
    #
    # arguments: input_size - int representing size of input
    #            hidden_size - number of nodes in the hidden layer
    #            num_classes - number of classes to classify
    #
    # return: none
    #
    # This method is the main function.
    #
    def __init__(self):

        # inherit the superclass properties/methods
        #
        super(Model, self).__init__()

        self.conv1 = nn.Conv1d(8, 64, 3,stride = 2) # 8 input channels, 64 output channels, 3x3 kernel, stride 1
        self.relu1 = nn.ReLU()
        self.conv2 = nn.Conv1d(64, 32, 3,stride = 2)
        self.relu2 = nn.ReLU()
        self.conv3= nn.Conv1d(32, 16, 3,stride = 2 )
        self.relu3 = nn.ReLU()
        self.maxpool = nn.MaxPool1d(2)
        self.fc1 = nn.Linear(2192, 64)
        self.relu4 = nn.ReLU()
        self.fc2 = nn.Linear(64, 32)
        self.relu5 = nn.ReLU()
        self.fc3 = nn.Linear(32, 6)
        #convolution to start and end with linear 

    def forward(self, data):
        data = data.permute(0, 2, 1)

        x = self.conv1(data)
        x = self.relu1(x)
        x = self.conv2(x)
        x = self.relu2(x)
        x = self.conv3(x)
        x = self.relu3(x)
        x = self.maxpool(x)
        x = x.view(x.size(0), -1)
        x = self.fc1(x)
        x = self.relu4(x)
        x = self.fc2(x)
        x = self.relu5(x)
        x = self.fc3(x)
        x = torch.sigmoid(x)
        return x

## Metrics

In [9]:
X.shape

(20000, 2200, 8)

In [16]:
model = Model()
model.load_state_dict(torch.load("/home/tud03114/finalproject/models/final_model_done.pth"))

X_train_torch = torch.from_numpy(X).float()
alg = "nn"
data = "eval"


In [14]:
#batch eval for memory instead of y_pred = model(torch.tensor(X).float())

with torch.no_grad(): 
    model.eval()

    y_pred = []
    for i in range(0, X.shape[0], 128):
        X_batch = torch.tensor(X[i:i+128]).float()
        y_pred.append(model(X_batch))
    y_pred = torch.cat(y_pred)

    
    
    #convert to numpy
    y_pred = y_pred.numpy().astype(int)
y_pred.shape  

(20000, 6)

In [10]:
diseases = ['1dAVb', 'RBBB', 'LBBB', 'SB', 'AF', 'ST']

In [17]:

def produce_hyp_files(y_pred, alg,data):
  df = pd.DataFrame(columns=diseases)
  for j,dis in enumerate(diseases):
      df[dis] = y_pred[:,j]
  df.to_csv(f'hyps/hyp_{alg}_{data}.csv',index=False)
  #y_test.to_csv(f'hyps/ref_{alg}_{data}.csv',index=False)
  #python score.py preds.csv labels.csv

produce_hyp_files(y_pred,alg,data)


In [32]:
#df = pd.DataFrame(columns=diseases)
#for j,dis in enumerate(diseases):
#    df[dis] = y_pred[:,j]
#df.to_csv('preds.csv',index=False)
#y_test.to_csv("labels.csv",index=False)
#python score.py preds.csv labels.csv

In [33]:
np.mean(y_pred)

0.12034166666666667

In [34]:
import subprocess
ref = "/home/tud03114/finalproject/hyps/ref_nn_dev.csv" 
hyp = "/home/tud03114/finalproject/hyps/hyp_nn_dev.csv"

subprocess.run(["python", "score.py",ref,hyp]) 

Metric 1: simple accuracy
 err / acc = 0.3941 / 0.6059

Metric 2: micro accuracy / precision / recall / f1
 micro acc / prec / rec / f1 = 0.8903 / 0.4866 / 0.5498 / 0.5163

Metric 3: macro accuracy / precision / recall / f1
  [1dAVb] acc / prec / rec / f1 = 0.8234 / 0.1085 / 0.1390 / 0.1218
  [RBBB] acc / prec / rec / f1 = 0.9256 / 0.8365 / 0.7240 / 0.7762
  [LBBB] acc / prec / rec / f1 = 0.9562 / 0.7077 / 0.8700 / 0.7805
  [SB] acc / prec / rec / f1 = 0.9597 / 0.7420 / 0.8512 / 0.7928
  [AF] acc / prec / rec / f1 = 0.8533 / 0.3345 / 0.4095 / 0.3682
  [ST] acc / prec / rec / f1 = 0.8234 / 0.1085 / 0.1390 / 0.1218
 macro acc / prec / rec / f1 = 0.8903 / 0.4729 / 0.5221 / 0.4936



CompletedProcess(args=['python', 'score.py', '/home/tud03114/finalproject/hyps/ref_nn_dev.csv', '/home/tud03114/finalproject/hyps/hyp_nn_dev.csv'], returncode=0)